In [4]:
import sys
import os

sys.path.append(os.path.abspath("../src"))
PROJECT_ROOT = os.getenv("PROJECT_ROOT")

In [2]:
from recommender.data_processors.mastery_features_processor import MasteryFeaturesProcessor
from recommender.data_loaders.summoner_match_loader import SummonerMatchLoader
from recommender.utils.riot_api_helper import RiotApiHelper
from recommender.utils.map_helper import MapHelper
from recommender.utils.data_utils import ChampionsFeaturesDataset
from recommender.utils.data_utils import MultiEpochsDataLoader
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OrdinalEncoder
from recommender.filters.two_tower import TwoTowerModel, TwoTowerRecommender

mfp = MasteryFeaturesProcessor()
rah = RiotApiHelper()
sml = SummonerMatchLoader()
mh = MapHelper()

In [3]:
puuid = "--EEhXPKpjfGXqRUXQeFUIrad-z3jgjyrwQj6Z49G4zWAK77gXCckScrJ9yxTxy91DXiJXWp_ka1Vg"

In [ ]:
ttr = TwoTowerRecommender()
await ttr.get_predicted_ratings(puuid)

Epoch 1, Loss: 360.1810915139281
Test MSE: 401.6459730921556
Epoch 2, Loss: 359.8307929448732
Test MSE: 402.6835973571884
Epoch 3, Loss: 359.92278432521954
Test MSE: 401.2512127886295
Model training completed in 69.97141027450562 seconds.


{6.242420673370361: 'Zyra'}

In [ ]:
df, le_user, le_champion = await mfp.async_load_encoded_ratings()
categorical_cols = ["summoner_rank", "summoner_lane", "champ_attack_type", "champ_adaptive_type"]
df[categorical_cols] = OrdinalEncoder().fit_transform(df[categorical_cols]).astype(int)

In [ ]:
train_df, test_df = train_test_split(df, test_size=0.2)
train_dataset = ChampionsFeaturesDataset(train_df)
test_dataset = ChampionsFeaturesDataset(test_df)

In [ ]:
train_loader = MultiEpochsDataLoader(train_dataset, batch_size=20, shuffle=True)
test_loader = MultiEpochsDataLoader(test_dataset, batch_size=20, shuffle=True)

In [ ]:

import torch
import torch.nn as nn

In [ ]:
ttr = TwoTowerRecommender()
ttm = TwoTowerModel()

In [ ]:
for a, b, c in train_loader:
    a = a
    b = b
    c = c
    break

In [ ]:
user = (torch.tensor([5]), torch.tensor([2]))

In [ ]:
ttm(a, b)

tensor([5.9841, 5.9841, 5.9841, 8.8454, 8.8454, 5.9841, 5.9841, 8.8454, 5.9841,
        5.9841, 5.9841, 5.9841, 8.8454, 5.9841, 8.8454, 5.9841, 8.8454, 5.9841,
        5.9841, 5.9841], grad_fn=<SumBackward1>)

In [ ]:
puuid = "--EEhXPKpjfGXqRUXQeFUIrad-z3jgjyrwQj6Z49G4zWAK77gXCckScrJ9yxTxy91DXiJXWp_ka1Vg"
summoner_df = df[df["puuid"] == puuid].iloc[0]
rank_ids = torch.tensor(summoner_df["summoner_rank"], dtype=torch.long)
lane_ids = torch.tensor(summoner_df["summoner_lane"], dtype=torch.long)
summoner_tuple = (rank_ids, lane_ids)

In [ ]:
champ_df = df[["champ_name", "champ_attack_type", "champ_adaptive_type"]].drop_duplicates().sort_values(by="champ_name")

# Step 1: Extract model input columns
attack_type_ids = torch.tensor(champ_df["champ_attack_type"].values, dtype=torch.long)
adaptive_type_ids = torch.tensor(champ_df["champ_adaptive_type"].values, dtype=torch.long)

# Step 2: Build champ_tensor_tuple
champ_tensor_tuple = (attack_type_ids, adaptive_type_ids)

In [ ]:
predicted_ratings = ttm(summoner_tuple, champ_tensor_tuple)
champ_order = torch.argsort(predicted_ratings, descending=True)
predicted_ratings_dict = {
    predicted_ratings[champ.item()].item(): le_champion.inverse_transform(
        [champ.item()]
    )[0]
    for champ in champ_order
}

In [ ]:
# champ_df[champ_df["champ_name"].isin(["Zoe","Zyra"])]
predicted_ratings_dict

{8.845425605773926: 'Zeri', 5.984121799468994: 'Zyra'}

In [ ]:
scores = ttm(user, champ_tensor_tuple)
scores

tensor([5.9841, 5.9841, 5.9841, 8.8454, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841,
        8.8454, 8.8454, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841,
        5.9841, 5.9841, 8.8454, 5.9841, 5.9841, 5.9841, 8.8454, 5.9841, 5.9841,
        5.9841, 8.8454, 5.9841, 5.9841, 5.9841, 8.8454, 5.9841, 5.9841, 5.9841,
        5.9841, 5.9841, 5.9841, 8.8454, 5.9841, 8.8454, 5.9841, 5.9841, 5.9841,
        5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 8.8454,
        8.8454, 5.9841, 5.9841, 8.8454, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841,
        5.9841, 5.9841, 5.9841, 8.8454, 5.9841, 8.8454, 5.9841, 5.9841, 5.9841,
        5.9841, 5.9841, 8.8454, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841,
        5.9841, 5.9841, 8.8454, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841,
        5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841,
        5.9841, 5.9841, 5.9841, 5.9841, 8.8454, 5.9841, 5.9841, 5.9841, 5.9841,
        5.9841, 5.9841, 5.9841, 5.9841, 

In [ ]:
ttr.train_and_evaluate_model(ttm, train_loader, test_loader)

Epoch 1, Loss: 371.31629758029567
Test MSE: 349.0486298964699
Epoch 2, Loss: 371.29821391878636
Test MSE: 349.1290726462619
Epoch 3, Loss: 371.2960356498384
Test MSE: 349.1041071587786
Epoch 4, Loss: 371.3208090800756
Test MSE: 349.27582577475346
Epoch 5, Loss: 371.32991223524436
Test MSE: 349.09402936064714
Epoch 6, Loss: 371.2974161155899
Test MSE: 349.05147106762627
Epoch 7, Loss: 371.3048209221027
Test MSE: 349.17107934481504
Epoch 8, Loss: 371.29333136802495
Test MSE: 349.0517142112937
Epoch 9, Loss: 371.3234202082278
Test MSE: 349.060121707771
Epoch 10, Loss: 371.31747973030474
Test MSE: 349.73511183157547
Model training completed in 77.09439849853516 seconds.


In [ ]:
ttm

TwoTowerModel(
  (summoner_tower): SummonerTower(
    (rank_factors): Embedding(10, 8)
    (lane_factors): Embedding(5, 8)
    (mlp): Sequential(
      (0): Linear(in_features=16, out_features=64, bias=True)
      (1): ReLU()
      (2): Linear(in_features=64, out_features=32, bias=True)
      (3): ReLU()
      (4): Linear(in_features=32, out_features=10, bias=True)
    )
  )
  (champ_tower): ChampTower(
    (attack_type_factors): Embedding(2, 8)
    (adaptive_type_factors): Embedding(2, 8)
    (mlp): Sequential(
      (0): Linear(in_features=16, out_features=64, bias=True)
      (1): ReLU()
      (2): Linear(in_features=64, out_features=32, bias=True)
      (3): ReLU()
      (4): Linear(in_features=32, out_features=10, bias=True)
    )
  )
)

In [ ]:
model = TwoTowerModel()
optimizer = torch.optim.Adam(model.parameters(), lr=1e-3)

# To update to negative sampling
criterion = nn.MSELoss()

for epoch in range(1):
    model.train()
    total_loss = 0
    for summoner_factors, champ_factors, ratings in train_loader:
        optimizer.zero_grad()
        preds = model(summoner_factors, champ_factors)
        loss = criterion(preds, ratings)
        loss.backward()
        optimizer.step()
        total_loss += loss.item()
    print(f"Epoch {epoch+1}, Loss: {total_loss / len(train_loader)}")  

[tensor([0, 0, 0, 1, 1]), tensor([0, 1, 1, 1, 1])]
[tensor([1, 1, 0, 1, 1]), tensor([1, 1, 1, 1, 0])]
[tensor([0, 0, 0, 0, 1]), tensor([1, 1, 1, 1, 1])]
[tensor([0, 1, 0, 0, 1]), tensor([1, 1, 0, 0, 0])]
[tensor([0, 1, 1, 1, 1]), tensor([1, 0, 1, 1, 0])]
[tensor([0, 0, 1, 0, 0]), tensor([1, 1, 0, 1, 1])]
[tensor([0, 0, 0, 1, 0]), tensor([1, 0, 1, 0, 0])]
[tensor([0, 0, 0, 0, 0]), tensor([0, 1, 1, 0, 0])]
[tensor([1, 1, 0, 1, 0]), tensor([1, 1, 1, 1, 1])]
[tensor([1, 0, 1, 1, 1]), tensor([0, 0, 1, 0, 0])]
[tensor([0, 1, 1, 0, 0]), tensor([0, 0, 1, 1, 1])]
[tensor([1, 1, 1, 1, 1]), tensor([1, 0, 1, 0, 0])]
[tensor([1, 0, 0, 1, 1]), tensor([1, 1, 1, 0, 0])]
[tensor([1, 0, 0, 1, 0]), tensor([1, 1, 0, 1, 1])]
[tensor([1, 0, 1, 1, 1]), tensor([1, 1, 0, 0, 1])]
[tensor([1, 1, 0, 1, 0]), tensor([0, 0, 1, 0, 1])]
[tensor([0, 1, 1, 1, 0]), tensor([1, 0, 0, 0, 0])]
[tensor([0, 1, 1, 0, 0]), tensor([0, 0, 1, 1, 1])]
[tensor([1, 0, 0, 1, 0]), tensor([0, 1, 0, 0, 1])]
[tensor([1, 1, 0, 1, 1]), tenso

In [ ]:
# Step 1: Build the df with column of lets say mode rank, mode lanes, roles, attack_types
# Step 2: Make train and test loader using TwoTowerChampionDataset
# Step 3: iterate for user_feattures, champ_features, rating in loader: preds = model(user_features, champ_features)

In [ ]:
puuid = "_2dRYSt03dHrJrRDcYImk2_umcnVSo8i-1WMun-j8YAFYk9CzauMu7WjQ8IJCY_RDWMopccQI_qfcw"
match_ids = rah.get_player_matches(puuid)